In [1]:
!pip install transformers

import requests

import pandas as pd

from bs4 import BeautifulSoup

from datetime import datetime

import pandas as pd

import re

from transformers import pipeline

from google.colab import drive

import pandas as pd

from pandas.io.formats.info import pprint_thing

from google.colab import drive

drive.mount('/content/drive')



Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.1/7.1 MB 58.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 24.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 88.9 MB/s eta 0:00:00
Mounted at /content/drive


In [2]:
import requests
from bs4 import BeautifulSoup
from transformers import pipeline
import pandas as pd
from tqdm import tqdm

def assess_sentiment_model(text, model_name):
    sentiment_analyzer = pipeline("sentiment-analysis", model=model_name)
    result = sentiment_analyzer(text)
    sentiment = result[0]['label']
    score = result[0]['score']
    return sentiment, score

def get_bbc_content(url):
    r = requests.get(url)
    soup = BeautifulSoup(r.content, "html.parser") 
    content = soup.find("div", attrs={"class": "gel-layout__item gel-2/3@l"})
    
    if content is None:
        content = soup.find("td", attrs={"class": "storybody"})
        if content is None:
            return None

    main_body = content.find_all('p')
    text = ""
    for i in main_body:
        text += i.text
    clean_text = text.replace('\n', ' ').replace('\xa0', '')
    return clean_text

def process_row(row, sentiment_models):
    content = get_bbc_content(row["url"])
    for model_name, sentiment_column in sentiment_models:
        sentiment_scores = []

        if content is not None:
            # Truncate or split the content into smaller chunks
            max_sequence_length = 512
            if len(content) > max_sequence_length:
                content_chunks = [content[i:i+max_sequence_length] for i in range(0, len(content), max_sequence_length)]
            else:
                content_chunks = [content]

            # Assess sentiment for each content chunk
            for chunk in content_chunks:
                sentiment, score = assess_sentiment_model(chunk, model_name)
                sentiment_scores.append(score)

        # Calculate average sentiment score
        if sentiment_scores:
            average_score = sum(sentiment_scores) / len(sentiment_scores)
            row[sentiment_column + "_average_score"] = average_score

    return row

def assess_sentiment(df):
    sentiment_models = [
        ("bert-base-uncased", "sentiment_bert"),
        ("roberta-base", "sentiment_roberta"),
        ("xlnet-base-cased", "sentiment_xlnet"),
        ("distilbert-base-uncased", "sentiment_distilbert")
    ]

    for _, sentiment_column in sentiment_models:
        df[sentiment_column + "_average_score"] = None

    total_rows = len(df)
    with tqdm(total=total_rows, desc="Processing Rows") as pbar:
        for index, row in df.iterrows():
            row = process_row(row, sentiment_models)
            df.loc[index] = row
            pbar.update(1)

            # Update progress bar description
            pbar.set_postfix({"Completed": index+1})

    return df


In [3]:
df21= pd.read_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_seperate_assessed_3.csv')


In [4]:
df_6 = assess_sentiment(df21[500:600])
df_6.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_6_FIRST_seperate_assessed_5.csv', index=False)

<ipython-input-2-7b3becf55e09>:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[sentiment_column + "_average_score"] = None
<ipython-input-2-7b3becf55e09>:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[sentiment_column + "_average_score"] = None
<ipython-input-2-7b3becf55e09>:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-d

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

Xformers is not installed correctly. If you want to use memorry_efficient_attention to accelerate training use the following command to install Xformers
pip install xformers.
Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a B

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.bias', 'roberta.pooler.dense.weight', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.dense.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.weight', 'classifie

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.bias', 'roberta.pooler.dense.weight', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.dense.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.weight', 'classifie

Some weights of the model checkpoint at xlnet-base-cased were not used when initializing XLNetForSequenceClassification: ['lm_loss.bias', 'lm_loss.weight']
- This IS expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of XLNetForSequenceClassification were not initialized from the model checkpoint at xlnet-base-cased and are newly initialized: ['sequence_summary.summary.bias', 'logits_proj.bias', 'logits_proj.weight', 'sequence_summary.summary.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions a

Some weights of the model checkpoint at xlnet-base-cased were not used when initializing XLNetForSequenceClassification: ['lm_loss.bias', 'lm_loss.weight']
- This IS expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of XLNetForSequenceClassification were not initialized from the model checkpoint at xlnet-base-cased and are newly initialized: ['sequence_summary.summary.bias', 'logits_proj.bias', 'logits_proj.weight', 'sequence_summary.summary.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions a

Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_layer_norm.weight', 'vocab_projector.bias', 'vocab_layer_norm.bias', 'vocab_projector.weight', 'vocab_transform.weight', 'vocab_transform.bias']
- This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias', 'pre_classifier

Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.weight', 'classifier.dense.bias', 'classifier.out_proj.weight', 'classifier.out_proj.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.bias', 'roberta.pooler.dense.weight', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.dense.bias']
- This IS expect

In [5]:
df_7 = assess_sentiment(df21[600:700])
df_7.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_7_FIRST_seperate_assessed_5.csv', index=False)

Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.bias', 'roberta.pooler.dense.weight', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.dense.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the ch

In [6]:
df_8 = assess_sentiment(df21[700:800])
df_8.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_8_FIRST_seperate_assessed_5.csv', index=False)

Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.weight', 'classifier.dense.bias', 'classifier.out_proj.weight', 'classifier.out_proj.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.bias', 'roberta.pooler.dense.weight', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.dense.bias']
- This IS expect

In [7]:
df_9 = assess_sentiment(df21[800:900])
df_9.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_9_FIRST_seperate_assessed_5.csv', index=False)

Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight']

In [8]:
df_10 = assess_sentiment(df21[900:])
df_10.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_10_FIRST_seperate_assessed_5.csv', index=False)

Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of XLNetForSequenceClassification were not initialized from the model checkpoint at xlnet-base-cased and are newly initialized: ['sequence_summary.summary.bias', 'logits_proj.bias', 'logits_proj.weight', 'sequence_summary.summary.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at xlnet-base-cased were not used when initializing XLNetForSequenceClassification: ['lm_loss.bias', 'lm_loss.weight']
- This IS expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertF

In [9]:
df_1000 = pd.concat([df_6, df_7, df_8, df_9, df_10])
df_1000
df_1000.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_SECOND_seperate_assessed_5.csv', index=False)

In [ ]:
df_1000.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_SECOND_seperate_assessed_5.csv', index=False)

In [10]:
import requests
from bs4 import BeautifulSoup
from transformers import pipeline
import pandas as pd
from tqdm import tqdm

def get_bbc_content(url):
    r = requests.get(url)
    soup = BeautifulSoup(r.content, "html.parser") 
    content = soup.find("div", attrs={"class": "gel-layout__item gel-2/3@l"})
    
    if content is None:
        content = soup.find("td", attrs={"class": "storybody"})
        if content is None:
            return None

    main_body = content.find_all('p')
    text = ""
    for i in main_body:
        text += i.text
    clean_text = text.replace('\n', ' ').replace('\xa0', '')
    return clean_text

def assess_bert_relevance(df):
    relevance_column = 'bert_relevance'
    model_name = 'bert-base-uncased'
    
    nlp = pipeline('text-classification', model=model_name)
    
    df[relevance_column] = None
    
    total_rows = len(df)
    
    with tqdm(total=total_rows, desc="Processing Rows") as pbar:
        for index, row in df.iterrows():
            content = get_bbc_content(row['url'])
            player_name = row['player']
            
            statement = f"{player_name} will be the MVP"
            
            relevance_score = nlp(statement, content)[0]['score']
            
            df.at[index, relevance_column] = relevance_score
            
            pbar.update(1)
            pbar.set_postfix({"Completed": index+1})
    
    return df


In [11]:
df_6 = assess_bert_relevance(df_6)
df_6.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_6_FIRST_seperate_assessed_6.csv', index=False)



Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

In [12]:
df_7 = assess_bert_relevance(df_7)
df_7.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_7_FIRST_seperate_assessed_6.csv', index=False)



Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

In [13]:
df_8 = assess_bert_relevance(df_8)
df_8.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_8_FIRST_seperate_assessed_6.csv', index=False)



Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

In [16]:
df_9 = assess_bert_relevance(df_9)
df_9.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_9_FIRST_seperate_assessed_6.csv', index=False)



Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

In [15]:
df_10 = assess_bert_relevance(df_10)
df_10.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_10_FIRST_seperate_assessed_6.csv', index=False)



Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

In [14]:
df_1000_f = pd.concat([df_6, df_7, df_8, df_9, df_10])
df_1000_f
df_1000.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_FIRST_seperate_assessed_6.csv', index=False)


In [17]:
df_500= pd.read_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_FIRST_seperate_assessed_6.csv')


In [21]:
df_2021_f = pd.concat([df_1000_f, df_500])

In [22]:
df_2021_f.to_csv('/content/drive/MyDrive/DS105L/bbc_news_season/bbc_2021_seperate_assessed_FN.csv', index=False)

In [23]:
df_2021_f

Unnamed: 0                                              title     date  \
500        4141  NBA: LeBron James handed first NBA suspension ...  2021-22   
501        4143  NBA: LeBron James scores 26 points against his...  2021-22   
502        4189  NBA: LeBron James suspended for Los Angeles La...  2021-22   
503        4193  NBA: LeBron James shines as LA Lakers beat Hou...  2021-22   
504        4341  NBA: Los Angeles Lakers beaten by New Orleans ...  2021-22   
..          ...                                                ...      ...   
507       11556  NFL play-offs: San Francisco 49ers, Kansas Cit...  2021-22   
508       11560  NFL play-offs: Kansas City Chiefs target third...  2021-22   
509       11640  NBA: Jazz end two-game losing streak, Antetoko...  2021-22   
510       11656  NFL: Miami Dolphins claim upset win over Balti...  2021-22   
511       11737  NFL: Russell Wilson joins Denver Broncos - 202...  2021-22   

                                                   url          player  \
500    https://www.bbc.co.uk/sport/basketball/59371603    LeBron James   
501    https://www.bbc.co.uk/sport/basketball/59101077    LeBron James   
502    https://www.bbc.co.uk/sport/basketball/59399534    LeBron James   
503    https://www.bbc.co.uk/sport/basketball/59146508    LeBron James   
504    https://www.bbc.co.uk/sport/basketball/60965085    LeBron James   
..                                                 ...             ...   
507  https://www.bbc.co.uk/sport/american-football/...   Elijah Bryant   
508  https://www.bbc.co.uk/sport/american-football/...   Elijah Bryant   
509    https://www.bbc.co.uk/sport/basketball/59200795  Justin Jackson   
510  https://www.bbc.co.uk/sport/american-football/...  Justin Jackson   
511  https://www.bbc.co.uk/sport/american-football/...  Justin Jackson   

     textblob_Sentiment  key_words_score sentiment_bert_average_score  \
500           -0.051212              1.0                     0.572849   
501            0.150668              1.0                     0.583822   
502           -0.004895              1.0                     0.569954   
503            0.106643              1.0                     0.537889   
504            0.051104              1.0                     0.543825   
..                  ...              ...                          ...   
507            0.110852              0.8                     0.601671   
508            0.072206              0.8                     0.571293   
509            0.163636              0.8                     0.556348   
510            0.182822              0.8                     0.614318   
511            0.127880              1.0                     0.581576   

    sentiment_roberta_average_score sentiment_xlnet_average_score  \
500                        0.525706                      0.607371   
501                        0.537027                      0.539689   
502                        0.528072                       0.60248   
503                        0.531168                      0.545369   
504                        0.521866                       0.64035   
..                              ...                           ...   
507                        0.534949                      0.591471   
508                         0.53432                      0.605299   
509                        0.513224                      0.545918   
510                        0.529136                      0.535386   
511                         0.53951                      0.590188   

    sentiment_distilbert_average_score bert_relevance  
500                           0.531891       0.506368  
501                           0.535961       0.506368  
502                           0.510645       0.506368  
503                           0.530356       0.506368  
504                           0.510085       0.506368  
..                                 ...            ...  
507                           0.529678            NaN  
508          